# Extract MODIS cloud mask dataset 

Requirements:

- A GOOGLE cloud project linked to your GOOGLE account


### My project 

Google account: gelieza.gk@gmail.com


cloud project ID: sample-project-452812 


cloud project name: Sample Project


In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import ee
import geemap
import math

In [ ]:
print("Hello from WSL!")

Hello from WSL!


In [3]:
# Authorization and initialization of the GEE
# OBS: You must create our own project on Google
# Authenticate Earth Engine
ee.Authenticate()
#
# Initialize Earth Engine
my_project_name = 'sample-project-452812' # use here the name of your own project on Google
ee.Initialize(project=my_project_name)

gio: https://code.earthengine.google.com/client-auth?scopes=https%3A//www.googleapis.com/auth/earthengine%20https%3A//www.googleapis.com/auth/cloud-platform%20https%3A//www.googleapis.com/auth/devstorage.full_control&request_id=UeMBPYJQBmCBHpt1XIoLt_GGCzk759q-O0fqcFVtURw&tc=BFPFdQ6IxmqqOH6ENg_TVFxsiFYHQtvj6kZnvblCQHg&cc=6QIvzjOfltypAKxI64kIcwt_I-cgzd4LMOFn-FwzVQU: Operation not supported



Successfully saved authorization token.


In [4]:
# Convert degree to radian
def deg2rad(deg):
    return deg * math.pi / 180

In [5]:
# Define the center of the bounding box (Bergen, Norway)
CENTER_LAT = 60.39
CENTER_LON = 5.33

# Approximate degree adjustments for 100km x 100km box
DEG_LAT_TO_KM = 111.412  # 1 degree latitude at 60° converted to km (https://en.wikipedia.org/wiki/Latitude)
DEG_LON_TO_KM = 111.317 * math.cos(deg2rad(CENTER_LAT))  # 1 degree longitude converted to km
LAT_OFFSET = 40 / DEG_LAT_TO_KM  # ~40km north/south, ~ 0.45
LON_OFFSET = 40 / DEG_LON_TO_KM  # ~40km east/west (varies with latitude, approximation), ~ 0.9

# Define the bounding box
BBOX = {
    "north": CENTER_LAT + LAT_OFFSET,
    "south": CENTER_LAT - LAT_OFFSET,
    "west": CENTER_LON - LON_OFFSET,
    "east": CENTER_LON + LON_OFFSET
}
# Geometry Rectangle of Form minLng, minLat, maxLng, maxLat
bergen_roi = ee.Geometry.Rectangle([BBOX["west"], BBOX["south"], BBOX["east"], BBOX["north"]])

Map = geemap.Map(center=[CENTER_LAT, CENTER_LON], zoom=8)

# Add the geometry to the map
Map.addLayer(bergen_roi, {"color": "red"}, "Bergen ROI")

# Display the map
Map

Map(center=[60.39, 5.33], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=SearchDataGUI…

In [6]:
# Function to extract cloud mask using bit 10 of state_1km band
def get_cloud(img):
    cld = img.select('state_1km').bitwiseAnd(1 << 10).eq(1 << 10)
    return img.addBands(cld.rename('cld'))

start_date = '2024-04-01'
end_date = '2025-04-01'
    
# Load MOD09GA and MYD09GA collections
mod_collection = ee.ImageCollection('MODIS/061/MOD09GA') \
    .filterDate(start_date, end_date) \
    .filterBounds(bergen_roi) \
    .map(get_cloud)

myd_collection = ee.ImageCollection('MODIS/061/MYD09GA') \
    .filterDate(start_date, end_date) \
    .filterBounds(bergen_roi) \
    .map(get_cloud)

# Merge the two collections
merged_collection = mod_collection.merge(myd_collection)

# (Optional) Select only the 'cld' band
cloud_mask_collection = merged_collection.select('cld')

# Function to add lat/lon bands to each image
def add_lat_lon(img):
    latlon = ee.Image.pixelLonLat()
    return img.addBands(latlon)

# Apply to cloud mask collection
cloud_mask_with_latlon = cloud_mask_collection.map(add_lat_lon)
cloud_mask_with_latlon

In [7]:
# Get first image
first_image = cloud_mask_with_latlon.first()

# Visualize latitude
Map = geemap.Map(center=[(BBOX["south"] + BBOX["north"]) / 2, (BBOX["west"] + BBOX["east"]) / 2], zoom=8)
Map.addLayer(first_image.select('cld'), {"min": 0, "max": 1, "palette": ["white", "blue"]}, "Cloud Mask")
Map.addLayer(bergen_roi, {"color": "red"}, "Bergen ROI")
Map

Map(center=[60.39, 5.33], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=SearchDataGUI…

In [10]:
# Function to extract only the image acquisition time
def extract_time(img):
    return ee.Feature(None, {
        'time': img.date().format('YYYY-MM-dd HH:mm')
    })

# Map over your image collection
timestamps_fc = cloud_mask_collection.map(extract_time)
timestamps_fc

In [14]:
# Convert FeatureCollection to Pandas DataFrame
df = geemap.ee_to_df(timestamps_fc) #todo: fix error 

# Convert 'time' column to datetime
df['time'] = pd.to_datetime(df['time'])
df.head()

TypeError: ee_object must be an ee.FeatureCollection

In [ ]:
# Extract hours
df['hour'] = df['time'].dt.hour

# Plot histogram of observation times
plt.figure(figsize=(10, 5))
plt.hist(df['hour'], bins=24, range=(0, 24), color='skyblue', edgecolor='black')
plt.title('MODIS Terra + Aqua Observation Time Distribution')
plt.xlabel('Hour of Day')
plt.ylabel('Number of Observations')
plt.xticks(range(0, 24))
plt.grid(axis='y', linestyle='--', alpha=0.7)
plt.show()